# Introduction

The objective is to study the different features of the cyber attack data and remove features that do not add value as inputs for our model.

## Import & data

### Import

In [1]:
import os
from pathlib import Path
if Path.cwd().name != "Ml_project":
    print(Path.cwd().name)
    os.chdir("./cours/Ml_project")
else:
    print("Already in Ml_project directory")

Already in Ml_project directory


In [2]:
import re
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import plotly.express as px
import plotly.graph_objects as go
import plotly.io as pio
import inspect

from IPython.display import Image
from IPython.core.display import HTML
from sklearn.decomposition import PCA
from sklearn.preprocessing import StandardScaler, OneHotEncoder
from plotly.subplots import make_subplots
from scipy.signal import find_peaks
from scipy.stats import linregress

from cyber_utils.parse_ua import list_ua_parser, ua_info_list
from cyber_utils.date_func import detect_peaks_and_slopes

In [3]:
palette = px.colors.qualitative.Plotly

### Data

In [4]:
data_path=Path("./data")
full_data = pd.read_csv(data_path.joinpath("cybersecurity_attacks.csv"))
full_data["Timestamp"] = pd.to_datetime(full_data["Timestamp"], format="%Y-%m-%d %H:%M:%S")
full_data = full_data.sort_values(by="Timestamp").reset_index(drop=True)
# full_data = full_data.sample(frac=0.1, axis = "index", random_state=42)

In [5]:
device_info = full_data["Device Information"].apply(lambda x: pd.Series(list_ua_parser(x)))
device_info.columns = ua_info_list

In [6]:
device_info.describe()

String Browser Name  \
count                                               40000        40000   
unique                                              32104            9   
top     Mozilla/5.0 (compatible; MSIE 6.0; Windows NT ...        Opera   
freq                                                   35         8049   

       Browser Version Browser Minor Browser Patch Browser Patch Minor  \
count            40000         40000         15074                8105   
unique              66           101           120                   1   
top                  9             0             5                   0   
freq              6679         26126          3283                8105   

        OS Name OS Version OS Version Minor OS Version Patch  \
count     40000      32829            14696            10682   
unique        5         21               13               10   
top     Windows         10                1                1   
freq      17953       7762             2328             2085   

       OS Version Patch Minor Device Brand Device Model Device Type  
count                       0        16322        16322       16322  
unique                      0            3            7           7  
top                       NaN        Apple          Mac         Mac  
freq                      NaN        11570         5796        5796

In [7]:
date_info = full_data["Timestamp"].apply(lambda x: pd.Series([x.year, x.month, x.day, x.hour, x.minute, x.second]))
date_info.columns = ["Year", "Month", "Day", "Hour", "Minute", "Second"]

In [8]:
date_info.describe()

Year         Month           Day          Hour        Minute  \
count  40000.000000  40000.000000  40000.000000  40000.000000  40000.000000   
mean    2021.411375      6.288275     15.629550     11.507350     29.511825   
std        1.085253      3.332979      8.771715      6.919122     17.360543   
min     2020.000000      1.000000      1.000000      0.000000      0.000000   
25%     2020.000000      3.000000      8.000000      5.000000     14.000000   
50%     2021.000000      6.000000     16.000000     12.000000     29.000000   
75%     2022.000000      9.000000     23.000000     17.000000     45.000000   
max     2023.000000     12.000000     31.000000     23.000000     59.000000   

             Second  
count  40000.000000  
mean      29.591300  
std       17.357387  
min        0.000000  
25%       14.000000  
50%       30.000000  
75%       45.000000  
max       59.000000

# Temporal Analysis

In [9]:

fig = make_subplots(rows=3, cols=2)
for i, name in enumerate(date_info.columns):
    temp_data = date_info.loc[:, name].sort_values()
    fig.add_trace(
        go.Histogram(x=temp_data, nbinsx=30, name=name),
        row=(i // 2) + 1,
        col=(i % 2) + 1
    )
fig.update_layout(height=800, width=1400, title_text="Date Information Distributions")
fig.update_xaxes(type = "category")
fig.show()

## Hour distribution

In [10]:
temp_data = date_info["Hour"].to_frame().merge(full_data["Attack Type"], left_index = True, right_index=True)
fig =px.histogram(temp_data, x="Hour", nbins=24, title="Hour Distribution", color = "Attack Type", barmode="group")
fig.update_xaxes(type = "category", categoryarray = list(range(24)))
fig.show()

We can see there is always one type with slighty more or less attacks than the other 2. <br>
The idea is to split by hour depending on the number of counts for each hour. The threshold is the mean of counts

In [11]:
date_counts = date_info["Hour"].value_counts().to_frame()
date_counts["Split"] = date_counts["count"] > date_counts["count"].mean()

temp_data["Split"] = temp_data["Hour"].apply(lambda x: True if date_counts.loc[x, "Split"] else False)

In [12]:
fig = make_subplots(rows = 2, cols=1)
for i, attack_type in enumerate(temp_data["Attack Type"].unique()):
    for j, split in enumerate(temp_data["Split"].unique()):
        sub_data = temp_data[(temp_data["Attack Type"] == attack_type) & (temp_data["Split"] == split)]
        sub_data = sub_data.sort_values(by="Hour")
        fig.add_trace(
            go.Histogram(x=sub_data["Hour"], nbinsx=30, name=f"Attack Type: {attack_type} - Split: {split}", marker_color=palette[i]),
        row = j+1, col=1)
fig.update_layout(height=600, title_text="Hour Distribution by Attack Type and Split")
fig.update_xaxes(type = "category", categoryarray=list(range(0,24)))
fig.update_layout()
fig.show()

It doesn't appear that one of the attack type as a pattern with more or less counts than the other 2. Vary for each hour

## Pattern Analysis - Detecting Slopes Before Peaks

Analysis to determine if there are temporal patterns showing positive slopes (increasing attack frequency) in the days/weeks before peaks occur for each attack type.

In [13]:
# Prepare daily aggregated data by attack type
daily_attacks = date_info[["Year", "Month", "Day"]].copy()
daily_attacks["Date"] = pd.to_datetime(daily_attacks[["Year", "Month", "Day"]])
daily_attacks = daily_attacks.merge(full_data["Attack Type"], left_index=True, right_index=True)
daily_attacks = daily_attacks.groupby(['Date', 'Attack Type']).size().reset_index(name='Count')

# Create a complete date range for each attack type (fill missing dates with 0)
all_dates = pd.date_range(start=daily_attacks['Date'].min(), end=daily_attacks['Date'].max(), freq='D')
attack_types = daily_attacks['Attack Type'].unique()

complete_data = []
for attack_type in attack_types:
    attack_data = daily_attacks[daily_attacks['Attack Type'] == attack_type].set_index('Date')
    complete_series = attack_data.reindex(all_dates, fill_value=0)
    complete_series['Attack Type'] = attack_type
    complete_data.append(complete_series.reset_index().rename(columns={'index': 'Date'}))

daily_attacks_complete = pd.concat(complete_data, ignore_index=True)
daily_attacks_complete = daily_attacks_complete.sort_values(['Attack Type', 'Date']).reset_index(drop=True)

In [14]:
temp_data = daily_attacks_complete.copy()
fig = make_subplots(rows=3, cols=1, shared_xaxes=True)
for i, attack_type in enumerate(temp_data["Attack Type"].unique()):
    sub_data = temp_data[temp_data["Attack Type"] == attack_type]
    fig.add_trace(
        go.Scatter(x=sub_data["Date"], y=sub_data["Count"], name=f"Attack Type: {attack_type}", marker_color=palette[i]),
        row= i+1, col=1
    )
fig.update_layout(
    title='Daily Attack Frequency by Attack Type',
    xaxis_title='Date',
    yaxis_title='Number of Attacks',
    height=900,
    hovermode='x unified'
)
fig.update_yaxes(fixedrange=True)
fig.show()

Doesn't look like there are patterns with peaks of attacks at 1st glance

In [15]:
temp_data.describe(percentiles=[0.1, 0.2, 0.3, 0.4, 0.5, 0.6, 0.7, 0.8, 0.9])

Date        Count
count                           4140  4140.000000
mean   2021-11-20 12:00:00.000000256     9.661836
min              2020-01-01 00:00:00     1.000000
10%              2020-05-17 21:36:00     6.000000
20%              2020-10-02 19:12:00     7.000000
30%              2021-02-17 16:48:00     8.000000
40%              2021-07-05 14:24:00     9.000000
50%              2021-11-20 12:00:00    10.000000
60%              2022-04-07 09:36:00    10.000000
70%              2022-08-23 07:12:00    11.000000
80%              2023-01-08 04:48:00    12.000000
90%              2023-05-26 02:24:00    14.000000
max              2023-10-11 00:00:00    23.000000
std                              NaN     3.150972

In [16]:
peak_analysis_results = {}
table_data = []

for attack_type in attack_types:
    attack_data = daily_attacks_complete[daily_attacks_complete['Attack Type'] == attack_type].copy()
    attack_data = attack_data.sort_values('Date').reset_index(drop=True)
    
    results = detect_peaks_and_slopes(attack_data, attack_type, window_days=[3, 7, 14, 21])
    peak_analysis_results[attack_type] = results
    
    # Collect data for table
    for window in [3, 7, 14, 21]:
        window_key = f'{window}d'
        analysis = results['slopes_analysis'][window_key]
        table_data.append({
            'Attack Type': attack_type,
            'Window': f'{window}d',
            'Peaks': results['num_peaks'],
            'Mean Slope (attacks/day)': round(analysis['mean_slope'], 3),
            'Mean Slope (%/day)': round(analysis['mean_slope_normalized'], 2),
            'Positive Slopes': analysis['positive_slopes'],
            'Negative Slopes': analysis['negative_slopes'],
            'Positive Ratio (%)': round(analysis['positive_ratio'], 1)
        })

# Display results in a formatted table
results_df = pd.DataFrame(table_data)
results_df

Attack Type Window  Peaks  Mean Slope (attacks/day)  Mean Slope (%/day)  \
0         DDoS     3d    361                    -0.837               -8.53   
1         DDoS     7d    361                    -0.201               -2.07   
2         DDoS    14d    361                    -0.049               -0.50   
3         DDoS    21d    361                    -0.023               -0.23   
4    Intrusion     3d    342                    -0.685               -7.32   
5    Intrusion     7d    342                    -0.185               -1.92   
6    Intrusion    14d    342                    -0.046               -0.47   
7    Intrusion    21d    342                    -0.021               -0.22   
8      Malware     3d    397                    -0.731               -7.29   
9      Malware     7d    397                    -0.154               -1.59   
10     Malware    14d    397                    -0.047               -0.49   
11     Malware    21d    397                    -0.019               -0.20   

    Positive Slopes  Negative Slopes  Positive Ratio (%)  
0               116              221                32.3  
1               125              223                34.7  
2               148              210                41.3  
3               146              210                40.9  
4               116              201                34.1  
5               123              208                36.1  
6               143              196                42.2  
7               148              189                43.9  
8               143              228                36.1  
9               149              232                37.7  
10              166              225                42.3  
11              161              227                41.4

- Positive Ratio > 50%: Attack frequency INCREASES before peaks (predictable buildup pattern)
- Positive Ratio < 50%: Attack frequency DECREASES or stays flat before peaks (sudden spikes)
- Positive Ratio ≈ 50%: No clear pattern (random/unpredictable behavior)

In [17]:
# Visualize peaks and slopes for each attack type
for i, attack_type in enumerate(attack_types):
    results = peak_analysis_results[attack_type]
    attack_data = daily_attacks_complete[daily_attacks_complete['Attack Type'] == attack_type].copy()
    attack_data = attack_data.sort_values('Date').reset_index(drop=True)
    
    fig = make_subplots(
        rows=2, cols=2,
        subplot_titles=('Time Series with Peaks', '7-Day Slope Distribution', 
                       '14-Day Slope Distribution', '21-Day Slope Distribution'),
        vertical_spacing=0.15,
        horizontal_spacing=0.1
    )
    
    # Plot 1: Time series with peaks highlighted
    fig.add_trace(
        go.Scatter(x=attack_data['Date'], y=attack_data['Count'],
                  mode='lines', name='Attack Frequency',
                  line=dict(color=palette[i], width=1.5)),
        row=1, col=1
    )
    fig.update_xaxes(title_text="Date", row=1, col=1)
    fig.update_yaxes(title_text="Attack Count", row=1, col=1)
    # Highlight peaks
    if results['num_peaks'] > 0:
        fig.add_trace(
            go.Scatter(x=results['peak_dates'], y=results['peak_values'],
                      mode='markers', name='Peaks',
                      marker=dict(color='red', size=10, symbol='star')),
            row=1, col=1
        )
    
    # Plot 2: 7-day slope distribution
    slopes_7d = results['slopes_analysis']['7d']['slopes_normalized']
    if slopes_7d:
        fig.add_trace(
            go.Histogram(x=slopes_7d, name='7-Day Slopes',
                        marker_color=palette[(i+1) % len(palette)],
                        nbinsx=20, showlegend=False),
            row=2, col=1
        )
        fig.add_vline(x=0, line_dash="dash", line_color="red", row=2, col=1)
    fig.update_xaxes(title_text="Slope (% change/day)", row=1, col=2)
    fig.update_yaxes(title_text="Frequency", row=1, col=2)

    # Plot 3: 14-day slope distribution
    slopes_14d = results['slopes_analysis']['14d']['slopes_normalized']
    if slopes_14d:
        fig.add_trace(
            go.Histogram(x=slopes_14d, name='14-Day Slopes',
                        marker_color=palette[(i+2) % len(palette)],
                        nbinsx=20, showlegend=False),
            row=2, col=2
        )
        fig.add_vline(x=0, line_dash="dash", line_color="red", row=2, col=2)
    fig.update_xaxes(title_text="Slope (% change/day)", row=2, col=1)
    fig.update_yaxes(title_text="Frequency", row=2, col=1)

    # Plot 4: 21-day slope distribution
    slopes_21d = results['slopes_analysis']['21d']['slopes_normalized']
    if slopes_21d:
        fig.add_trace(
            go.Histogram(x=slopes_21d, name='21-Day Slopes',
                        marker_color=palette[(i+3) % len(palette)],
                        nbinsx=20, showlegend=False),
            row=1, col=2
        )
        fig.add_vline(x=0, line_dash="dash", line_color="red", row=1, col=2)
    fig.update_xaxes(title_text="Slope (% change/day)", row=2, col=2)
    fig.update_yaxes(title_text="Frequency", row=2, col=2)

    # Update layout
    fig.update_layout(
        title_text=f'Peak Analysis for {attack_type} Attacks',
        height=700,
        showlegend=True
    )

    fig.show()

In [18]:
# Summary comparison across all attack types
summary_data = []
for attack_type in attack_types:
    results = peak_analysis_results[attack_type]
    for window in [3, 7, 14, 21]:
        window_key = f'{window}d'
        analysis = results['slopes_analysis'][window_key]
        summary_data.append({
            'Attack Type': attack_type,
            'Window (days)': window,
            'Mean Slope (% change/day)': analysis['mean_slope_normalized'],
            'Positive Slope Ratio (%)': analysis['positive_ratio'],
            'Number of Peaks': results['num_peaks']
        })

summary_df = pd.DataFrame(summary_data)

# Visualize summary
fig = make_subplots(
    rows=2, cols=2,
    subplot_titles=('Mean Slope Before Peaks', 'Positive Slope Ratio',
                   'Number of Peaks Detected', 'Slope Statistics Heatmap'),
    specs=[[{}, {}], [{}, {}]],
    vertical_spacing=0.15
)

# Chart 1: Mean slope
for i, attack_type in enumerate(attack_types):
    data = summary_df[summary_df['Attack Type'] == attack_type]
    fig.add_trace(
        go.Bar(x=data['Window (days)'], y=data['Mean Slope (% change/day)'],
              name=attack_type, marker_color=palette[i]),
        row=1, col=1
    )

fig.update_xaxes(title_text="Window (days)", row=1, col=1, type="category")
fig.update_yaxes(title_text="Mean Slope (%/day)", row=1, col=1)

# Chart 2: Positive slope ratio
for i, attack_type in enumerate(attack_types):
    data = summary_df[summary_df['Attack Type'] == attack_type]
    fig.add_trace(
        go.Bar(x=data['Window (days)'], y=data['Positive Slope Ratio (%)'],
              name=attack_type, marker_color=palette[i], showlegend=False),
        row=1, col=2
    )
# Add 50% reference line
fig.add_hline(y=50, line_dash="dash", line_color="gray", 
             annotation_text="50% (random)", row=1, col=2)

fig.update_xaxes(title_text="Window (days)", row=1, col=2, type="category")
fig.update_yaxes(title_text="Positive Slope Ratio (%)", row=1, col=2)

# Chart 3: Number of peaks
peaks_data = summary_df.groupby('Attack Type')['Number of Peaks'].first()
fig.add_trace(
    go.Bar(x=peaks_data.index, y=peaks_data.values,
          marker_color=[palette[i] for i in range(len(attack_types))],
          showlegend=False),
    row=2, col=1
)
fig.update_xaxes(title_text="Attack Type", row=2, col=1)
fig.update_yaxes(title_text="Number of Peaks", row=2, col=1)

# Chart 4: Heatmap
heatmap_data = summary_df.pivot(index='Attack Type', columns='Window (days)', values='Positive Slope Ratio (%)')
fig.add_trace(
    go.Heatmap(z=heatmap_data.values, x=heatmap_data.columns, y=heatmap_data.index,
              colorscale='RdYlGn', zmid=50, colorbar=dict(title='Ratio %'),
              text=heatmap_data.values.round(1), texttemplate='%{text}%', textfont={"size":10}, showscale=False),
    row=2, col=2
)

fig.update_xaxes(title_text="Windows (days)", row=2, col=2, type="category")

fig.update_layout(
    title_text='Summary: Temporal Patterns Across Attack Types',
    height=800,
    barmode='group'
)

fig.show()

nothing relevant to analyse. When a "peak" appears there is no positive slope before. It is something you would expect from cyber-attacks: they discover a break use it progressively before being detected.

## Device Analysis

In [19]:
device_counts = device_info["Browser Name"].value_counts().to_frame()

temp_data = device_info.merge(full_data["Attack Type"], left_index = True, right_index=True)
px.histogram(temp_data, x="Browser Name", title="Browser Name Distribution", color = "Attack Type", barmode="group")

### Basic Analysis

In [20]:
temp_data["Mobile Flag"] = temp_data["Browser Name"].apply(lambda x: "Mobile" if ("Mobile" in x or "iOS" in x) else "Desktop")
fig = make_subplots(rows = 1, cols=2)

fig.add_trace(
    go.Histogram(x=temp_data.loc[temp_data["Mobile Flag"]=="Mobile", "Browser Name"], name="Mobile"),
    row = 1,
    col=1)
fig.add_trace(
    go.Histogram(x=temp_data.loc[temp_data["Mobile Flag"]=="Desktop", "Browser Name"], name="Desktop"),
    row = 1,
    col=2
)
fig.show()

There are a lot more of attacks on Safari mobile compare to other mobile browser
For desktop browser, it is tied between Opera and Internet Explorer

In [21]:
px.histogram(temp_data, x="Mobile Flag", title="Attack type distribution", color = "Attack Type", barmode="group")

But not a lot of variance between each type of attack 

In [22]:

for i, name in enumerate(device_info["Browser Name"].unique()):
    temp_data = device_info[device_info["Browser Name"]==name].merge(full_data["Attack Type"], left_index = True, right_index=True)
    fig = px.histogram(temp_data, x="Browser Name", title=f"Browser Version Distribution for {name}", color = "Browser Version", barmode="group")
    fig.show()
    plt.close()

### Chrome browser analysis

Lot of information in the browser version, could be useful to split based on the release date of the version.

In [23]:
chrome_version_file = "chrome_versions.csv"
chrome_version_data = pd.read_csv(data_path.joinpath(chrome_version_file), sep = ";")
chrome_version_data["release_date"] = pd.to_datetime(chrome_version_data["release_date"], format = "%d/%m/%Y")
chrome_version_data["version"] = chrome_version_data["version"].str.split(".",n = 1).str[0]

In [24]:
temp_data = device_info.reset_index(names=["Original Index"])
temp_data = temp_data[temp_data["Browser Name"]=="Chrome"].merge(chrome_version_data, left_on="Browser Version", right_on = "version", how="left")
temp_data = temp_data.merge(full_data["Attack Type"], left_on="Original Index", right_index=True)

fig = px.histogram(temp_data, x="version", title=f"Chrome Version Distribution", color = "Attack Type", barmode="group")
fig.update_xaxes(type = "category", categoryarray = sorted(chrome_version_data["version"].unique(), key=lambda x: int(x)))
fig.update_layout(width=1200, showlegend=False)
fig.show()

In [25]:
temp_data["before"] = temp_data["release_date"] < pd.Timestamp("2016-01-01")
fig = px.histogram(temp_data, x="before", title=f"Chrome Version Release Date Distribution", color = "Attack Type", barmode="group")
fig.update_xaxes(type = "category")
fig.show()

We can see a difference in the type of attack if we split chrome version according to release date but not so much

### Analysis by browser

In [26]:
temp_data = device_info.reset_index(names=["Original Index"])
temp_data = temp_data.merge(full_data["Attack Type"], left_index = True, right_index=True)

# Merge all browser variants (remove Mobile, iOS suffixes)
mobile = r" Mobile|Mobile| iOS|iOS "
temp_data["Browser Base"] = temp_data["Browser Name"].str.replace(mobile, "", regex = True)
temp_data["Browser Base"] = temp_data["Browser Base"].str.strip()

# Group by Browser Base and Attack Type to get counts
attack_counts = temp_data.groupby(["Browser Base", "Attack Type"]).size().reset_index(name="Count")

# Create bar chart
browsers = sorted(attack_counts["Browser Base"].unique())
fig = go.Figure()

for i, attack_type in enumerate(attack_counts["Attack Type"].unique()):
    attack_data = attack_counts[attack_counts["Attack Type"] == attack_type]
    fig.add_trace(
        go.Bar(x=attack_data["Browser Base"], y=attack_data["Count"], 
               name=attack_type, marker_color=palette[i])
    )

fig.update_layout(
    title="Number of Attacks by Browser and Attack Type (Desktop + Mobile + iOS merged)",
    xaxis_title="Browser",
    yaxis_title="Number of Attacks",
    barmode='group',
    height=600,
    xaxis={'categoryorder':'total descending'}
)
fig.show()


In [27]:
# Display summary table
print("\n=== Attack Counts by Browser and Attack Type ===")
summary_pivot = attack_counts.pivot(index="Browser Base", columns="Attack Type", values="Count").fillna(0)
summary_pivot["Total"] = summary_pivot.sum(axis=1)
summary_pivot = summary_pivot.sort_values("Total", ascending=False)
print(summary_pivot)

# Display percentages
print("\n=== Attack Type Distribution (%) by Browser ===")
percentage_pivot = summary_pivot.drop("Total", axis=1).div(summary_pivot["Total"], axis=0) * 100
print(percentage_pivot.round(2))


=== Attack Counts by Browser and Attack Type ===
Attack Type   DDoS  Intrusion  Malware  Total
Browser Base                                 
Chrome        2679       2690     2736   8105
Opera         2770       2673     2606   8049
IE            2713       2582     2700   7995
Safari        2597       2644     2729   7970
Firefox       2669       2676     2536   7881

=== Attack Type Distribution (%) by Browser ===
Attack Type    DDoS  Intrusion  Malware
Browser Base                           
Chrome        33.05      33.19    33.76
Opera         34.41      33.21    32.38
IE            33.93      32.30    33.77
Safari        32.58      33.17    34.24
Firefox       33.87      33.96    32.18


In [28]:
# Split each browser by minor version
temp_data = device_info.reset_index(names=["Original Index"])
temp_data = temp_data.merge(full_data["Attack Type"], left_index = True, right_index=True)

# Merge all browser variants (remove Mobile, iOS suffixes)
temp_data["Browser Base"] = temp_data["Browser Name"].str.replace(" Mobile", "", regex=False)
temp_data["Browser Base"] = temp_data["Browser Base"].str.replace(" iOS", "", regex=False)
temp_data["Browser Base"] = temp_data["Browser Base"].str.strip()

# Group by Browser Base, Browser Minor version, and Attack Type
version_counts = temp_data.groupby(["Browser Base", "Browser Minor", "Attack Type"]).size().reset_index(name="Count")

# Create a subplot for each browser
browsers = sorted(version_counts["Browser Base"].unique())
num_browsers = len(browsers)
rows = (num_browsers + 1) // 3  # Calculate rows needed for 3 columns
cols = 3

fig = make_subplots(rows=rows, cols=cols, 
                    subplot_titles=[f'{browser}' for browser in browsers],
                    vertical_spacing=0.12,
                    horizontal_spacing=0.1)

# Plot each browser
for idx, browser in enumerate(browsers):
    row = (idx // 3) + 1
    col = (idx % 3) + 1
    
    browser_data = version_counts[version_counts["Browser Base"] == browser]
    
    # Plot by attack type
    for i, attack_type in enumerate(browser_data["Attack Type"].unique()):
        attack_data = browser_data[browser_data["Attack Type"] == attack_type]
        fig.add_trace(
            go.Bar(x=attack_data["Browser Minor"], y=attack_data["Count"], 
                   name=attack_type, marker_color=palette[i], 
                   legendgroup=attack_type, showlegend=(idx==0)),
            row=row, col=col
        )
    
    # Sort x-axis by minor version number
    fig.update_xaxes(type="category", 
                    categoryarray=sorted(browser_data["Browser Minor"].unique(), 
                                       key=lambda x: int(x) if str(x).isdigit() else 0),
                    title_text="Browser Minor Version",
                    row=row, col=col)
    fig.update_yaxes(title_text="Count", row=row, col=col)

fig.update_layout(height=400*rows,
                  width=400 * rows + 200,
                  title_text="Attack Counts by Browser Minor Version and Attack Type (All variants merged)", 
                  barmode='group',
                  showlegend=False)
fig.show()


Group by browser doesn't add value

In [29]:
# Summary statistics by browser and minor version - Combined into single dataframe
print("\n=== Browser Minor Version Statistics by Attack Type ===")

all_browser_stats = []

for browser in browsers:
    browser_data = version_counts[version_counts["Browser Base"] == browser]
    
    # Create pivot table for this browser
    browser_pivot = browser_data.pivot(index="Browser Minor", columns="Attack Type", values="Count").fillna(0)
    browser_pivot["Total"] = browser_pivot.sum(axis=1)
    browser_pivot = browser_pivot.sort_values("Total", ascending=False)
    
    # Get top 10 and add browser name
    top_10 = browser_pivot.head(10).copy()
    top_10.insert(0, "Browser", browser)
    top_10.insert(1, "Minor Version", top_10.index)
    
    all_browser_stats.append(top_10)

# Combine all browsers into single dataframe
combined_stats = pd.concat(all_browser_stats, ignore_index=True)

# Reorder columns for better readability
column_order = ["Browser", "Minor Version"] + [col for col in combined_stats.columns if col not in ["Browser", "Minor Version"]]
combined_stats = combined_stats[column_order]

print(f"\nTop 10 minor versions by total attacks for each browser:")
combined_stats


=== Browser Minor Version Statistics by Attack Type ===

Top 10 minor versions by total attacks for each browser:


Attack Type        Browser Minor Version  DDoS  Intrusion  Malware  Total
0                   Chrome             0  2679       2690     2736   8105
1                  Firefox             0  1160       1117     1086   3363
2                  Firefox             6   569        619      592   1780
3                  Firefox             8   583        575      533   1691
4                  Firefox             3    49         64       52    165
5                  Firefox             5    54         57       49    160
6                  Firefox             9    60         48       49    157
7                  Firefox             4    46         58       44    148
8                  Firefox             1    51         43       47    141
9                  Firefox             2    47         51       43    141
10                 Firefox             7    50         44       41    135
11                      IE             0  2713       2582     2700   7995
12           Mobile Safari             0   886        924      846   2656
13                   Opera            37    42         35       49    126
14                   Opera            15    34         31       45    110
15                   Opera            75    43         35       31    109
16                   Opera            89    39         28       39    106
17                   Opera            85    34         41       31    106
18                   Opera            50    28         44       33    105
19                   Opera            46    41         31       32    104
20                   Opera            32    32         43       29    104
21                   Opera            59    32         27       44    103
22                   Opera            25    38         33       29    100
23                  Safari             0  1282       1308     1417   4007
24                  Safari             1   429        412      466   1307

# Traffic Analysis

## Network Analysis

### First analysis

In [30]:
network_data = full_data[["Attack Type", "Traffic Type", "Protocol", "Packet Type"]]

# Create subplots for each network feature
features = [col for col in network_data.columns if col != "Attack Type"]
fig = make_subplots(
    rows=1, cols=3,
    subplot_titles=tuple(features)
)



for idx, feature in enumerate(features, start=1):
    feature_counts = network_data.groupby([feature, "Attack Type"]).size().reset_index(name="Count")
    
    for i, attack_type in enumerate(network_data["Attack Type"].unique()):
        attack_data = feature_counts[feature_counts["Attack Type"] == attack_type]
        fig.add_trace(
            go.Bar(
                x=attack_data[feature],
                y=attack_data["Count"],
                name=attack_type,
                marker_color=palette[i % len(palette)],
                legendgroup=attack_type,
                showlegend=(idx == 1)
            ),
            row=1, col=idx
        )
    
    fig.update_xaxes(title_text=feature, row=1, col=idx)
    fig.update_yaxes(title_text="Count", row=1, col=idx)

fig.update_layout(
    title="Attack Counts by Network Features",
    barmode='group',
    height=500,
    width=1200,
    showlegend=False
)

fig.show()

In [31]:
# Calculate percentage difference between max and min attack counts for each feature
all_features_data = []

features = ["Traffic Type", "Protocol", "Packet Type"]

for feature in features:
    # Group by feature and attack type
    feature_counts = network_data.groupby([feature, "Attack Type"]).size().reset_index(name="Count")
    feature_pivot = feature_counts.pivot(index=feature, columns="Attack Type", values="Count").fillna(0)
    
    # Calculate max and min for each feature value
    feature_pivot["Max"] = feature_pivot.max(axis=1)
    feature_pivot["Min"] = feature_pivot.min(axis=1)
    feature_pivot["Total"] = feature_pivot.sum(axis=1)
    feature_pivot["Max-Min Diff"] = feature_pivot["Max"] - feature_pivot["Min"]
    feature_pivot["Diff %"] = ((feature_pivot["Max"] - feature_pivot["Min"]) / feature_pivot["Total"] * 100).round(2)
    
    # Add feature name and value to the dataframe
    feature_pivot["Feature"] = feature
    feature_pivot["Feature Value"] = feature_pivot.index
    
    # Append to list
    all_features_data.append(feature_pivot.reset_index(drop=True))

# Combine all features into one dataframe
features_comparison = pd.concat(all_features_data, ignore_index=True)

# Reorder columns for better readability
cols_order = ["Feature", "Feature Value"] + [col for col in features_comparison.columns if col not in ["Feature", "Feature Value"]]
features_comparison = features_comparison[cols_order]

# Display the combined dataframe
features_comparison

Attack Type       Feature Feature Value  DDoS  Intrusion  Malware   Max   Min  \
0            Traffic Type           DNS  4528       4426     4422  4528  4422   
1            Traffic Type           FTP  4389       4453     4422  4453  4389   
2            Traffic Type          HTTP  4511       4386     4463  4511  4386   
3                Protocol          ICMP  4508       4460     4461  4508  4460   
4                Protocol           TCP  4438       4397     4437  4438  4397   
5                Protocol           UDP  4482       4408     4409  4482  4408   
6             Packet Type       Control  6679       6755     6803  6803  6679   
7             Packet Type          Data  6749       6510     6504  6749  6504   

Attack Type  Total  Max-Min Diff  Diff %  
0            22326           106    0.47  
1            22106            64    0.29  
2            22257           125    0.56  
3            22397            48    0.21  
4            22107            41    0.19  
5            22189            74    0.33  
6            33719           124    0.37  
7            33016           245    0.74

Difference between min and max for each feature represents only around 0.5% of total data.
==> Difference are really small

### Feature combination analysis

In [32]:
# Pivot to show attack types as columns for easier comparison
attack_pivot = network_data.pivot_table(
    index=["Traffic Type", "Protocol", "Packet Type"],  
    columns="Attack Type",
    aggfunc=len,
    fill_value=0
)
# Sort by Traffic Type first
attack_pivot = attack_pivot.sort_index(level=0)

# Create subplots for each tuple using attack_pivot, grouped by Traffic Type

# Get unique traffic types to determine rows
traffic_types = attack_pivot.index.get_level_values(0).unique()
rows = len(traffic_types)

# Get max number of combinations per traffic type to determine columns
max_cols = max([len(attack_pivot.loc[tt]) for tt in traffic_types])

# Create subplots
fig = make_subplots(
    rows=rows, cols=max_cols,
    subplot_titles=[f"{idx[0]} | {idx[1]} | {idx[2]}" 
                    for idx in attack_pivot.index],
    vertical_spacing=0.15,
    horizontal_spacing=0.08
)

# Get attack type columns (exclude 'Total')
attack_types = [col for col in attack_pivot.columns if col != 'Total']

# Plot each tuple
idx = 0
for row_idx, traffic_type in enumerate(traffic_types, start=1):
    # Get all combinations for this traffic type
    traffic_data = attack_pivot.loc[traffic_type]
    
    # Handle case where there's only one combination (returns Series instead of DataFrame)
    if isinstance(traffic_data, pd.Series):
        traffic_data = traffic_data.to_frame().T
    
    for col_idx, (tuple_index, row_data) in enumerate(traffic_data.iterrows(), start=1):
        # Plot bars for each attack type
        for i, attack_type in enumerate(attack_types):
            fig.add_trace(
                go.Bar(
                    x=[attack_type],
                    y=[row_data[attack_type]],
                    name=attack_type,
                    marker_color=palette[i % len(palette)],
                    legendgroup=attack_type,
                    showlegend=(idx == 0)  # Only show legend for first subplot
                ),
                row=row_idx, col=col_idx
            )
        
        fig.update_xaxes(title_text="Attack Type", row=row_idx, col=col_idx)
        fig.update_yaxes(title_text="Count", row=row_idx, col=col_idx)
        idx += 1

fig.update_layout(
    height=400 * rows,
    width = 200 * max_cols + 200,
    title={
        'text': "Attack Counts by (Traffic Type, Protocol, Packet Type) Tuples",
        'y': 0.98,
        'x': 0.5,
        'xanchor': 'center',
        'yanchor': 'top'
    },
    showlegend=False
)

fig.show()

We can see the difference between type of attack is a bit more visible than when we look at each feature individually

In [33]:
# Get attack type columns (exclude 'Total')
attack_type_cols = attack_pivot.columns

# Add total column
attack_pivot["Total"] = attack_pivot.sum(axis=1)

# Calculate percentages for each tuple (row-wise)
for attack_type in attack_type_cols:
    attack_pivot[f"{attack_type} %"] = (attack_pivot[attack_type] / attack_pivot['Total'] * 100).round(2)


# Calculate difference between max and min percentage for each tuple (row-wise)
percentage_cols = [f"{attack_type} %" for attack_type in attack_type_cols]
attack_pivot['Max-Min Diff %'] = (attack_pivot[percentage_cols].max(axis=1) - attack_pivot[percentage_cols].min(axis=1)).round(2)

# Reorder columns to show count and percentage together
new_order = []
for attack_type in attack_type_cols:
    new_order.append(attack_type)
    new_order.append(f"{attack_type} %")
new_order.extend(['Total', 'Max-Min Diff %'])

attack_pivot = attack_pivot[new_order]

attack_pivot

Attack Type                        DDoS  DDoS %  Intrusion  Intrusion %  \
Traffic Type Protocol Packet Type                                         
DNS          ICMP     Control       809   34.32        778        33.01   
                      Data          754   34.97        702        32.56   
             TCP      Control       729   33.14        724        32.91   
                      Data          755   33.36        733        32.39   
             UDP      Control       715   32.57        753        34.31   
                      Data          766   34.74        736        33.38   
FTP          ICMP     Control       720   32.32        753        33.80   
                      Data          721   33.41        708        32.81   
             TCP      Control       726   32.56        782        35.07   
                      Data          730   34.06        714        33.32   
             UDP      Control       740   32.58        748        32.94   
                      Data          752   33.66        748        33.48   
HTTP         ICMP     Control       771   33.48        777        33.74   
                      Data          733   32.91        742        33.32   
             TCP      Control       736   32.92        726        32.47   
                      Data          762   34.64        718        32.64   
             UDP      Control       733   33.06        714        32.21   
                      Data          776   35.65        709        32.57   

Attack Type                        Malware  Malware %  Total  Max-Min Diff %  
Traffic Type Protocol Packet Type                                             
DNS          ICMP     Control          770      32.67   2357            1.65  
                      Data             700      32.47   2156            2.50  
             TCP      Control          747      33.95   2200            1.04  
                      Data             775      34.25   2263            1.86  
             UDP      Control          727      33.12   2195            1.74  
                      Data             703      31.88   2205            2.86  
FTP          ICMP     Control          755      33.89   2228            1.57  
                      Data             729      33.78   2158            0.97  
             TCP      Control          722      32.38   2230            2.69  
                      Data             699      32.62   2143            1.44  
             UDP      Control          783      34.48   2271            1.90  
                      Data             734      32.86   2234            0.80  
HTTP         ICMP     Control          755      32.78   2303            0.96  
                      Data             752      33.77   2227            0.86  
             TCP      Control          774      34.62   2236            2.15  
                      Data             720      32.73   2200            2.00  
             UDP      Control          770      34.73   2217            2.52  
                      Data             692      31.79   2177            3.86

In [34]:
print(attack_pivot["Max-Min Diff %"].max())
print(attack_pivot["Max-Min Diff %"].min())
print(attack_pivot["Max-Min Diff %"].mean())

3.86
0.8
1.8538888888888887


We do have a slight diff between max and min count. Mean is 1.8% compare to 0.5% before

### More network features

In [35]:
# Add network-related features to the tuple analysis (excluding port features)
# Features: Traffic Type, Protocol, Packet Type, Packet Length (categorized), Payload Length, Payload Word Count
network_data = full_data[["Attack Type", "Traffic Type", "Protocol", "Packet Type",
                          "Packet Length", "Payload Data"]].copy()

# Create Payload features from text
print("Creating Payload features from text data...")
network_data["Payload Length"] = network_data["Payload Data"].str.len()
network_data["Payload Word Count"] = network_data["Payload Data"].str.split().str.len()

# Show Packet Statistics
print("\nPayload statistics:")
print(network_data[["Payload Length", "Payload Word Count", "Packet Length"]].describe())
print("\n")

Creating Payload features from text data...

Payload statistics:
       Payload Length  Payload Word Count  Packet Length
count    40000.000000        40000.000000   40000.000000
mean       141.173875           18.807425     781.452725
std         36.526330            5.031886     416.044192
min         22.000000            3.000000      64.000000
25%        114.000000           15.000000     420.000000
50%        144.000000           19.000000     782.000000
75%        172.000000           23.000000    1143.000000
max        199.000000           33.000000    1500.000000




From this we can define some bins for each features
We take values close to the Q & Q3 values

In [36]:
network_data["Packet Length Category"] = pd.cut(
    network_data["Packet Length"],
    bins=[0, 450, 1150, float('inf')],
    labels=["Small (0-450)", "Medium (450-1150)", "Large (1150+)"]
)

# Categorize Payload Length based on quantiles
network_data["Payload Length Category"] = pd.cut(
    network_data["Payload Length"],
    bins=[0, 100, 175, float('inf')],
    labels=["Short (0-100)", "Medium (100-175)", "Long (175+)"]
)

# Categorize Payload Word Count
network_data["Payload Word Count Category"] = pd.cut(
    network_data["Payload Word Count"],
    bins=[0, 15, 25, float('inf')],
    labels=["Few (0-15)", "Some (15-25)", "Many (25+)"]
)

# Drop the raw Payload Data column as we now have categorized features
network_data = network_data.drop(columns=["Payload Data"])

# Pivot to show attack types as columns
network_pivot = network_data.pivot_table(
    index=["Traffic Type", "Protocol", "Packet Type", "Packet Length Category",
           "Payload Length Category", "Payload Word Count Category"],
    columns="Attack Type",
    aggfunc=len,
    fill_value=0
)

# Add total column
network_pivot["Total"] = network_pivot.sum(axis=1)

print("=== Attack Counts by Network Features ===")
print(f"\nTotal unique network feature combinations: {len(network_pivot)}")
print(f"\nTop 20 combinations by total attacks:\n")
temp_data = network_pivot.sort_values("Total", ascending=False)
temp_data.head(20)

=== Attack Counts by Network Features ===

Total unique network feature combinations: 352

Top 20 combinations by total attacks:



/tmp/ipykernel_1198/2414435942.py:25: FutureWarning:

The default value of observed=False is deprecated and will change to observed=True in a future version of pandas. Specify observed=False to silence this warning and retain the current behavior



Packet Length  \
Attack Type                                                                                                           DDoS   
Traffic Type Protocol Packet Type Packet Length Category Payload Length Category Payload Word Count Category                 
DNS          ICMP     Control     Medium (450-1150)      Medium (100-175)        Some (15-25)                        218.0   
HTTP         UDP      Control     Medium (450-1150)      Medium (100-175)        Some (15-25)                        197.0   
DNS          TCP      Data        Medium (450-1150)      Medium (100-175)        Some (15-25)                        175.0   
FTP          ICMP     Control     Medium (450-1150)      Medium (100-175)        Some (15-25)                        171.0   
             UDP      Control     Medium (450-1150)      Medium (100-175)        Some (15-25)                        167.0   
                      Data        Medium (450-1150)      Medium (100-175)        Some (15-25)                        191.0   
             TCP      Data        Medium (450-1150)      Medium (100-175)        Some (15-25)                        176.0   
HTTP         ICMP     Control     Medium (450-1150)      Medium (100-175)        Some (15-25)                        168.0   
FTP          TCP      Control     Medium (450-1150)      Medium (100-175)        Some (15-25)                        155.0   
HTTP         UDP      Data        Medium (450-1150)      Medium (100-175)        Some (15-25)                        179.0   
DNS          TCP      Control     Medium (450-1150)      Medium (100-175)        Some (15-25)                        187.0   
HTTP         TCP      Data        Medium (450-1150)      Medium (100-175)        Some (15-25)                        184.0   
                      Control     Medium (450-1150)      Medium (100-175)        Some (15-25)                        159.0   
FTP          ICMP     Data        Medium (450-1150)      Medium (100-175)        Some (15-25)                        170.0   
DNS          ICMP     Data        Medium (450-1150)      Medium (100-175)        Some (15-25)                        187.0   
             UDP      Control     Medium (450-1150)      Medium (100-175)        Some (15-25)                        168.0   
                      Data        Medium (450-1150)      Medium (100-175)        Some (15-25)                        173.0   
HTTP         ICMP     Data        Medium (450-1150)      Medium (100-175)        Some (15-25)                        158.0   
DNS          TCP      Data        Small (0-450)          Medium (100-175)        Some (15-25)                        116.0   
HTTP         ICMP     Data        Small (0-450)          Medium (100-175)        Some (15-25)                        110.0   

                                                                                                                        \
Attack Type                                                                                                  Intrusion   
Traffic Type Protocol Packet Type Packet Length Category Payload Length Category Payload Word Count Category             
DNS          ICMP     Control     Medium (450-1150)      Medium (100-175)        Some (15-25)                    184.0   
HTTP         UDP      Control     Medium (450-1150)      Medium (100-175)        Some (15-25)                    179.0   
DNS          TCP      Data        Medium (450-1150)      Medium (100-175)        Some (15-25)                    195.0   
FTP          ICMP     Control     Medium (450-1150)      Medium (100-175)        Some (15-25)                    192.0   
             UDP      Control     Medium (450-1150)      Medium (100-175)        Some (15-25)                    208.0   
                      Data        Medium (450-1150)      Medium (100-175)        Some (15-25)                    184.0   
             TCP      Data        Medium (450-1150)      Medium (100-175)        Some (15-25)                   

In [37]:
# For each combination of (Traffic Type, Protocol, Packet Type), 
# show top 10 full network feature combinations

# Get unique combinations of first 3 features
unique_combos = network_pivot.index.droplevel([3, 4, 5]).unique()

# Get attack type columns (exclude 'Total')
attack_types = [col for col in network_pivot.columns if col != ("Total","")]

# Create subplots - one for each (Traffic Type, Protocol, Packet Type) combination
num_combos = len(unique_combos)
rows = (num_combos + 2) // 3  # 3 columns per row
cols = min(3, num_combos)

fig = make_subplots(
    rows=rows,
    cols=cols,
    subplot_titles=[f"{c[0]} | {c[1]} | {c[2]}" for c in unique_combos],
    vertical_spacing=0.1,
    horizontal_spacing=0.05
)

for idx, combo in enumerate(unique_combos):
    row = (idx // 3) + 1
    col = (idx % 3) + 1
    
    # Get top 10 full combinations for this (Traffic Type, Protocol, Packet Type)
    combo_data = network_pivot.loc[combo].sort_values("Total", ascending=False).head(10)
    
    # Create short labels for the remaining features
    labels = [f"{idx[0][:5]}|{idx[1][:5]}|{idx[2][:5]}" for idx in combo_data.index]
    
    # Plot bars for each attack type
    for i, attack_type in enumerate(attack_types):
        fig.add_trace(
            go.Bar(
                x=labels,
                y=combo_data[attack_type],
                name=f"({attack_type[0]},{attack_type[1]})",
                marker_color=palette[i % len(palette)],
                legendgroup=f"({attack_type[0]},{attack_type[1]})",
                showlegend=False
            ),
            row=row, col=col
        )
    
    fig.update_xaxes(title_text="Pkt Len | Payload Len | Word Count", row=row, col=col, tickangle=-45)
    fig.update_yaxes(title_text="Count", row=row, col=col)

fig.update_layout(
    height=400 * rows,
    width=1600,
    title={
        'text': "Top 10 Full Network Feature Combinations<br>For Each (Traffic Type | Protocol | Packet Type)",
        'y': 0.99,
        'x': 0.5,
        'xanchor': 'center',
        'yanchor': 'top'
    },
    barmode='group',
    showlegend=False
)

fig.show()

We can clearly differences between each. <br>
But data might be too small to be usable <br>
Plus it only show the top 10 show what do we do with the rest??

In [38]:
# Calculate percentage for each attack type according to network features
network_percentage = network_pivot.copy()

# Get attack type columns (exclude 'Total')
attack_type_cols = [col for col in network_percentage.columns if col != 'Total']

# Calculate percentages for each combination (row-wise)
for attack_type in attack_type_cols:
    network_percentage[f"{attack_type} %"] = (network_percentage[attack_type] / network_percentage['Total'] * 100).round(2)

# Calculate difference between max and min percentage for each combination (row-wise)
percentage_cols = [f"{attack_type} %" for attack_type in attack_type_cols]
network_percentage['Max-Min Diff %'] = (network_percentage[percentage_cols].max(axis=1) - network_percentage[percentage_cols].min(axis=1)).round(2)

# Reorder columns to show count and percentage together
new_order = []
for attack_type in attack_type_cols:
    new_order.append(attack_type)
    new_order.append(f"{attack_type} %")
new_order.extend(['Total', 'Max-Min Diff %'])

network_percentage = network_percentage[new_order]
network_percentage = network_percentage.sort_values(["Total", "Max-Min Diff %"], ascending=False)
network_percentage.head(50)
network_percentage.iloc[0:50,7].describe()

KeyError: '["(\'Packet Length\', \'DDoS\') %", "(\'Packet Length\', \'Intrusion\') %", "(\'Packet Length\', \'Malware\') %", "(\'Payload Length\', \'DDoS\') %", "(\'Payload Length\', \'Intrusion\') %", "(\'Payload Length\', \'Malware\') %", "(\'Payload Word Count\', \'DDoS\') %", "(\'Payload Word Count\', \'Intrusion\') %", "(\'Payload Word Count\', \'Malware\') %", "(\'Total\', \'\') %", \'Total\', \'Max-Min Diff %\'] not in index'

In [ ]:
network_percentage.iloc[0:50,7].describe()

For the top 50 combinaisons by total attacks, the maximum difference in attack type percentages is quite high, indicating that certain network feature combinations are strongly associated with specific attack types. <br>
This suggests that attackers may be leveraging particular network characteristics to optimize their attack strategies. <br>
Further analysis could help identify these patterns and inform defensive measures.

## Detection Analysis

### First Analysis

In [39]:
detection_data = full_data[["Attack Type", "Malware Indicators", "Alerts/Warnings", "Action Taken", "IDS/IPS Alerts", "Log Source", "Firewall Logs"]]
detection_data = detection_data.fillna("Unknown")
# Create subplots for each detection feature
features = [col for col in detection_data.columns if col != "Attack Type"]
num_features = len(features)
fig = make_subplots(
    rows=num_features // 3 + (1 if num_features % 3 else 0) , cols=3,
)
for idx, feature in enumerate(features):
    row = (idx // 3) + 1
    col = (idx % 3) + 1
    
    feature_counts = detection_data.groupby([feature, "Attack Type"]).size().reset_index(name="Count")
    
    for i, attack_type in enumerate(detection_data["Attack Type"].unique()):
        attack_data = feature_counts[feature_counts["Attack Type"] == attack_type]
        fig.add_trace(
            go.Bar(
                x=attack_data[feature],
                y=attack_data["Count"],
                name=attack_type,
                marker_color=palette[i % len(palette)],
                legendgroup=attack_type,
                showlegend=(idx == 0)
            ),
            row=row, col=col
        )
    
    fig.update_xaxes(title_text=feature, row=row, col=col)
    fig.update_yaxes(title_text="Count", row=row, col=col)
fig.update_layout(
    title="Attack Counts by Detection Features",
    barmode='group',
    height=400 * (num_features // 3 + (1 if num_features % 3 else 0)),
    width=1200,
    showlegend=False
)
fig.show()

### Combined Detection Features Analysis

Similar to network data analysis, let's combine all detection features to identify patterns that better discriminate between attack types.

In [40]:
# Pivot to show attack types as columns for combined detection features
detection_pivot = detection_data.pivot_table(
    index=["Malware Indicators", "Alerts/Warnings", "Action Taken", "IDS/IPS Alerts", "Log Source", "Firewall Logs"],
    columns="Attack Type",
    aggfunc=len,
    fill_value=0
)

# Sort by index
detection_pivot = detection_pivot.sort_index(level=0)

# Add total column
detection_pivot["Total"] = detection_pivot.sum(axis=1)

print("=== Attack Counts by Combined Detection Features ===")
print(f"\nTotal unique detection feature combinations: {len(detection_pivot)}")
print(f"\nTop 20 combinations by total attacks:\n")
temp_data = detection_pivot.sort_values("Total", ascending=False)
temp_data.head(20)

=== Attack Counts by Combined Detection Features ===

Total unique detection feature combinations: 96

Top 20 combinations by total attacks:



Attack Type                                                                              DDoS  \
Malware Indicators Alerts/Warnings Action Taken IDS/IPS Alerts Log Source Firewall Logs         
Unknown            Unknown         Ignored      Unknown        Firewall   Log Data        159   
IoC Detected       Unknown         Logged       Alert Data     Server     Log Data        150   
                                                Unknown        Firewall   Unknown         151   
Unknown            Alert Triggered Blocked      Unknown        Firewall   Log Data        153   
IoC Detected       Unknown         Blocked      Unknown        Server     Unknown         146   
Unknown            Unknown         Blocked      Unknown        Firewall   Unknown         157   
                                   Ignored      Alert Data     Server     Log Data        151   
IoC Detected       Alert Triggered Blocked      Alert Data     Server     Log Data        150   
                   Unknown         Blocked      Alert Data     Server     Log Data        156   
                                                               Firewall   Log Data        144   
Unknown            Alert Triggered Ignored      Alert Data     Firewall   Unknown         156   
                   Unknown         Logged       Alert Data     Server     Unknown         172   
                   Alert Triggered Logged       Unknown        Firewall   Unknown         152   
IoC Detected       Alert Triggered Logged       Unknown        Firewall   Unknown         135   
Unknown            Alert Triggered Blocked      Unknown        Firewall   Unknown         155   
                   Unknown         Ignored      Unknown        Server     Log Data        149   
                   Alert Triggered Logged       Unknown        Firewall   Log Data        131   
IoC Detected       Unknown         Ignored      Alert Data     Server     Log Data        143   
Unknown            Unknown         Logged       Alert Data     Firewall   Log Data        160   
                                   Ignored      Unknown        Server     Unknown         147   

Attack Type                                                                              Intrusion  \
Malware Indicators Alerts/Warnings Action Taken IDS/IPS Alerts Log Source Firewall Logs              
Unknown            Unknown         Ignored      Unknown        Firewall   Log Data             148   
IoC Detected       Unknown         Logged       Alert Data     Server     Log Data             159   
                                                Unknown        Firewall   Unknown              159   
Unknown            Alert Triggered Blocked      Unknown        Firewall   Log Data             127   
IoC Detected       Unknown         Blocked      Unknown        Server     Unknown              157   
Unknown            Unknown         Blocked      Unknown        Firewall   Unknown              148   
                                   Ignored      Alert Data     Server     Log Data             144   
IoC Detected       Alert Triggered Blocked      Alert Data     Server     Log Data             157   
                   Unknown         Blocked      Alert Data     Server     Log Data             151   
                                                               Firewall   Log Data             153   
Unknown            Alert Triggered Ignored      Alert Data     Firewall   Unknown              135   
                   Unknown         Logged       Alert Data     Server     Unknown              150   
                   Alert Triggered Logged       Unknown        Firewall   Unknown              147   
IoC Detected       Alert Triggered Logged       Unknown        Firewall   Unknown              138   
Unknown            Alert Triggered Blocked      Unknown        Firewall   Unknown              140   
                   Unknown         Ignored      Unknown        Server     Log Data             146   
                   Alert Trig

In [41]:
# Calculate percentage for each attack type according to detection features
detection_percentage = detection_pivot.copy()

# Get attack type columns (exclude 'Total')
attack_type_cols = [col for col in detection_percentage.columns if col != 'Total']

# Calculate percentages for each combination (row-wise)
for attack_type in attack_type_cols:
    detection_percentage[f"{attack_type} %"] = (detection_percentage[attack_type] / detection_percentage['Total'] * 100).round(2)

# Calculate difference between max and min percentage for each combination (row-wise)
percentage_cols = [f"{attack_type} %" for attack_type in attack_type_cols]
detection_percentage['Max-Min Diff %'] = (detection_percentage[percentage_cols].max(axis=1) - detection_percentage[percentage_cols].min(axis=1)).round(2)

# Reorder columns to show count and percentage together
new_order = []
for attack_type in attack_type_cols:
    new_order.append(attack_type)
    new_order.append(f"{attack_type} %")
new_order.extend(['Total', 'Max-Min Diff %'])

detection_percentage = detection_percentage[new_order]
detection_percentage = detection_percentage.sort_values(["Total", "Max-Min Diff %"], ascending=False)

print("=== Detection Feature Combination Statistics ===")
print(f"\n\nTop 50 combinations by total attacks:")
detection_percentage.head(50)

=== Detection Feature Combination Statistics ===


Top 50 combinations by total attacks:


Attack Type                                                                              DDoS  \
Malware Indicators Alerts/Warnings Action Taken IDS/IPS Alerts Log Source Firewall Logs         
Unknown            Unknown         Ignored      Unknown        Firewall   Log Data        159   
IoC Detected       Unknown         Logged       Alert Data     Server     Log Data        150   
                                                Unknown        Firewall   Unknown         151   
Unknown            Alert Triggered Blocked      Unknown        Firewall   Log Data        153   
                   Unknown         Blocked      Unknown        Firewall   Unknown         157   
IoC Detected       Unknown         Blocked      Unknown        Server     Unknown         146   
Unknown            Unknown         Ignored      Alert Data     Server     Log Data        151   
IoC Detected       Alert Triggered Blocked      Alert Data     Server     Log Data        150   
                   Unknown         Blocked      Alert Data     Server     Log Data        156   
                                                               Firewall   Log Data        144   
Unknown            Unknown         Logged       Alert Data     Server     Unknown         172   
                   Alert Triggered Ignored      Alert Data     Firewall   Unknown         156   
                                   Logged       Unknown        Firewall   Unknown         152   
IoC Detected       Alert Triggered Logged       Unknown        Firewall   Unknown         135   
Unknown            Alert Triggered Blocked      Unknown        Firewall   Unknown         155   
                   Unknown         Ignored      Unknown        Server     Log Data        149   
                   Alert Triggered Logged       Unknown        Firewall   Log Data        131   
IoC Detected       Unknown         Ignored      Alert Data     Server     Log Data        143   
Unknown            Unknown         Logged       Alert Data     Firewall   Log Data        160   
IoC Detected       Unknown         Blocked      Unknown        Firewall   Unknown         128   
Unknown            Unknown         Ignored      Unknown        Server     Unknown         147   
IoC Detected       Alert Triggered Blocked      Alert Data     Firewall   Unknown         154   
                                   Ignored      Unknown        Server     Log Data        141   
Unknown            Unknown         Blocked      Alert Data     Firewall   Unknown         138   
IoC Detected       Alert Triggered Ignored      Unknown        Firewall   Log Data        125   
Unknown            Alert Triggered Ignored      Unknown        Firewall   Log Data        128   
IoC Detected       Unknown         Blocked      Unknown        Firewall   Log Data        149   
                                   Ignored      Unknown        Firewall   Unknown         164   
                                   Blocked      Alert Data     Firewall   Unknown         155   
                   Alert Triggered Ignored      Alert Data     Firewall   Unknown         152   
Unknown            Alert Triggered Logged       Unknown        Server     Unknown         157   
                                   Blocked      Alert Data     Firewall   Log Data        143   
                                                               Server     Log Data        143   
IoC Detected       Unknown         Logged       Alert Data     Firewall   Unknown         130   
                   Alert Triggered Logged       Unknown        Server     Unknown         152   
                   Unknown         Ignored      Alert Data     Firewall   Unknown         148   
Unknown            Alert Triggered Ignored      Unknown        Server     Unknown         137   
                   Unknown         Blocked      Unknown        Firewall   Log Data        165   
                   Alert Triggered Ignored      Unknown        Server     Log Data        155   
IoC Detected       Aler

In [ ]:
print(f"\nMax-Min Diff % statistics for top 50 combinations:")
detection_percentage.iloc[0:min(50, len(detection_percentage)), 7].describe()

### Top 10 Combinations: Malware Indicators, Alerts/Warnings, IDS/IPS Alerts

Focusing on three key detection features to identify the most common attack patterns.

In [42]:
# For each combination of (Malware Indicators, Alerts/Warnings, IDS/IPS Alerts), 
# show top 10 full detection feature combinations

# Create full detection pivot (all 6 features) - reuse from earlier or recreate
detection_full_pivot = detection_data.pivot_table(
    index=["Malware Indicators", "Alerts/Warnings", "IDS/IPS Alerts", "Action Taken", "Log Source", "Firewall Logs"],
    columns="Attack Type",
    aggfunc=len,
    fill_value=0
)
detection_full_pivot["Total"] = detection_full_pivot.sum(axis=1)

# Get unique combinations of first 3 features
unique_combos = detection_full_pivot.index.droplevel([3, 4, 5]).unique()

# Get attack type columns (exclude 'Total')
attack_types = [col for col in detection_full_pivot.columns if col != 'Total']

# Create subplots - one for each (Malware Indicators, Alerts/Warnings, IDS/IPS Alerts) combination
num_combos = len(unique_combos)
rows = (num_combos + 2) // 3  # 3 columns per row
cols = min(3, num_combos)

fig = make_subplots(
    rows=rows,
    cols=cols,
    subplot_titles=[f"{c[0]} | {c[1]} | {c[2]}" for c in unique_combos],
    vertical_spacing=0.15,
    horizontal_spacing=0.05
)

for idx, combo in enumerate(unique_combos):
    row = (idx // 3) + 1
    col = (idx % 3) + 1
    
    # Get top 10 full combinations for this (Malware Indicators, Alerts/Warnings, IDS/IPS Alerts)
    combo_data = detection_full_pivot.loc[combo].sort_values("Total", ascending=False).head(10)
    
    # Create short labels for the remaining features
    labels = [f"{idx[0][:5]}|{idx[1][:5]}|{idx[2][:5]}" for idx in combo_data.index]
    
    # Plot bars for each attack type
    for i, attack_type in enumerate(attack_types):
        fig.add_trace(
            go.Bar(
                x=labels,
                y=combo_data[attack_type],
                name=attack_type,
                marker_color=palette[i % len(palette)],
                legendgroup=attack_type,
                showlegend=False
            ),
            row=row, col=col
        )
    
    fig.update_xaxes(title_text="Action | Log Source | Firewall", row=row, col=col, tickangle=-45)
    fig.update_yaxes(title_text="Count", row=row, col=col)

fig.update_layout(
    height=400 * rows,
    width=1600,
    title={
        'text': "Top 10 Full Detection Feature Combinations<br>For Each (Malware Indicators | Alerts/Warnings | IDS/IPS Alerts)",
        'y': 0.98,
        'x': 0.5,
        'xanchor': 'center',
        'yanchor': 'top'
    },
    barmode='group',
    showlegend=True
)

fig.show()